In [1]:
import os 

os.environ['AWS_PROFILE'] = 'admin'
os.environ['HAVEN_DATABASE'] = 'haven'

import plotly.express as px
import pandas as pd
import numpy as np
import h3

from mirrorverse.utils import read_data_w_cache

# Model Evaluation

## Helpful Stuff

In [2]:
MODELS = {
    'A': ('3_1_1', 'ab17d4ce30981b9d7630da4d7adbf7fd7cb88a9bfee2b37ed60254e097e8ffdc'),
    'B': ('3_1_3', 'e875c3a83c56925e0537b30c6f64d3219ffcd41c2298490d69eec4c25899119c'),
    'C': ('3_1_4', '00cf23b296999368ea18b82e33b8687c51e8c35e876afd325e26317cb69ea45b'),
    'D': ('3_7_2', 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'),
}

## Overall Model Results

In [3]:
dfs = []
for model_name, (model_id, run_id) in MODELS.items():
    sql = f'''
    with likelihoods as (
        select
            _individual,
            '{model_name}' as model,
            _train, 
            avg(ln(probability)) as nll
        from 
            chinook_depth_inference_{model_id}
        where 
            run_id = '{run_id}'
            and _selected
        group by 
            1, 2, 3
    )
    select
        model,
        _train,
        avg(nll) as nll
    from 
        likelihoods
    group by 
        1, 2
    '''
    dfs.append(read_data_w_cache(sql))


sql = f'''
with probabilities as (
    select
        _individual,
        _decision,
        _train, 
        1.0 / cast(count(*) as double) as probability
    from 
        chinook_depth_inference_{model_id}
    where 
        run_id = '{run_id}'
    group by 
        1, 2, 3
), likelihoods as (
    select
        _individual,
        'Null' as model,
        _train, 
        avg(ln(probability)) as nll
    from 
        probabilities
    group by 
        1, 2, 3
)
select
    model,
    _train,
    avg(nll) as nll
from 
    likelihoods
group by 
    1, 2
'''
dfs.append(read_data_w_cache(sql))

data = pd.concat(dfs).sort_values(['_train', 'model']).reset_index(drop=True)
print(data.shape)
data

(10, 3)


model  _train       nll
0     A   False -1.457210
1     B   False -1.367708
2     C   False -1.352352
3     D   False -1.340310
4  Null   False -1.740250
5     A    True -1.412052
6     B    True -1.330207
7     C    True -1.312613
8     D    True -1.293438
9  Null    True -1.834539

## Depth Skew

In [4]:
model_name, (model_id, run_id) = next(iter(MODELS.items()))

sql = f'''
select
    depth_bin,
    count(*) as count
from 
    chinook_depth_inference_{model_id}
where
    run_id = '{run_id}'
    and _selected
group by 
    1
'''
data = read_data_w_cache(sql)
data['proportion'] = data['count'] / data['count'].sum()
data.sort_values('depth_bin', ascending=True)

depth_bin   count  proportion
0       25.0  231392    0.464131
5       50.0   82924    0.166331
4       75.0   64968    0.130314
6      100.0   48221    0.096723
7      150.0   50407    0.101107
8      200.0   15607    0.031305
9      250.0    3121     0.00626
1      300.0    1396      0.0028
3      400.0     509    0.001021
2      500.0       4    0.000008

In [5]:
sql = f'''
select
    depth_bin,
    sum(probability) as count
from 
    chinook_depth_inference_3_7_2
where
    run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
group by 
    1
'''
data = read_data_w_cache(sql)
data['proportion'] = data['count'] / data['count'].sum()
data.sort_values('depth_bin', ascending=True)

depth_bin          count  proportion
8       25.0  227475.140625    0.456274
1       50.0   81738.210938    0.163952
3       75.0   63048.332031    0.126464
2      100.0   53791.726562    0.107897
6      150.0   48895.320312    0.098075
4      200.0   18759.195312    0.037628
7      250.0    3875.935303    0.007774
9      300.0     788.164001    0.001581
0      400.0     151.065765    0.000303
5      500.0      25.908079    0.000052

In [6]:
data[data['depth_bin'] <= 100].sum()

depth_bin        250.000000
count         426053.406250
proportion         0.854587
dtype: float64

## Seasonality

In [92]:
color_discrete_map = {
    "25.0": "#1b9e77",  # Green
    "50.0": "#d95f02",  # Orange
    "75.0": "#7570b3",  # Purple
    "100.0": "#e7298a",  # Pink
    "150.0": "#66a61e",  # Olive Green
    "200.0": "#e6ab02",  # Yellow-Orange
    "250.0": "#a6761d",  # Brown
    "300.0": "#666666",  # Gray
    "400.0": "#1f78b4",  # Blue
    "500.0": "#a6cee3",  # Light Blue
}

In [93]:
model_id = '3_7_2'
run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
sql = f'''
select
    extract(month from time) as month,
    depth_bin,
    count(*) as count
from 
    chinook_depth_inference_{model_id}
where
    run_id = '{run_id}'
    and _selected
group by 
    1, 2
'''
actuals = read_data_w_cache(sql)
actuals['monthly_count'] = actuals.groupby('month')['count'].transform('sum')
actuals['proportion'] = actuals['count'] / actuals['monthly_count']
actuals['depth_bin'] = actuals['depth_bin'].astype(str)
actuals['case'] = 'actual'
px.bar(
    actuals, x='month', y='proportion', color='depth_bin', 
    color_discrete_map=color_discrete_map,
    category_orders={'depth_bin': color_discrete_map.keys()},
    title="Actual Proportion per Depth Bin by Month (Val)"
)

In [94]:
model_id = '3_7_2'
run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
sql = f'''
select
    extract(month from time) as month,
    depth_bin,
    sum(probability) as count
from 
    chinook_depth_inference_{model_id}
where
    run_id = '{run_id}'
group by 
    1, 2
'''
val = read_data_w_cache(sql)
val['monthly_count'] = val.groupby('month')['count'].transform('sum')
val['proportion'] = val['count'] / val['monthly_count']
val['depth_bin'] = val['depth_bin'].astype(str)
val['case'] = 'predicted'
px.bar(
    val, x='month', y='proportion', color='depth_bin', 
    color_discrete_map=color_discrete_map,
    category_orders={'depth_bin': color_discrete_map.keys()},
    title="Predicted Proportion per Depth Bin by Month (Val)"
)

In [96]:
df = pd.concat([val, actuals])
MONTHS = {
    1: 'Jan',
    2: 'Feb',
    3: 'Mar',
    4: 'Apr',
    5: 'May',
    6: 'Jun',
    7: 'Jul',
    8: 'Aug',
    9: 'Sep',
    10: 'Oct',
    11: 'Nov',
    12: 'Dec'
}
df["month"] = df["month"].apply(lambda m: MONTHS[m])
plot_df = df.rename(columns={'proportion': 'Proportion', 'depth_bin': 'Depth Bin (m)', 'month': 'Month', 'case': 'Case'})
plot_df['Case'] = plot_df['Case'].apply(lambda c: c.capitalize())
fig = px.bar(
    plot_df, x='Month', y='Proportion', color='Depth Bin (m)', 
    color_discrete_map=color_discrete_map,
    category_orders={'Depth Bin (m)': color_discrete_map.keys(), "Case": ["Actual", "Predicted"], "Month": list(MONTHS.values())},
    #title="Proportion per Depth Bin by Month",
    facet_row="Case", height=500, width=800
)
fig.show()

In [97]:
fig.write_image("fig2_seasonality.png", format="png", scale=2)

## Diel

In [19]:
model_id = '3_7_2'
run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'

sql = f'''
select
    extract(month from time) as month,
    cos_sun,
    sin_sun,
    _train,
    case 
        when depth_bin = 25 then 'shallow'
        else 'deep' 
    end as _case,
    sum(case when _selected then 1.0 else 0.0 end) as num_selected,
    sum(probability) as expected_num_selected
from 
    chinook_depth_inference_{model_id}
where
    run_id = '{run_id}'
group by 
    1, 2, 3, 4, 5
'''
data = read_data_w_cache(sql)
data['radians'] = np.arctan2(data['sin_sun'], data['cos_sun'])
data['radians'] = round(data['radians'] * 5) / 5
data = data.groupby(['month', '_train', 'radians', '_case'])[['num_selected', 'expected_num_selected']].sum().reset_index()
data['total_num_selected'] = data.groupby(['month', '_train', 'radians'])['num_selected'].transform('sum')
data['proportion'] = data['num_selected'] / data['total_num_selected']
data['predicted_proportion'] = data['expected_num_selected'] / data['total_num_selected']

data = pd.concat([
    data[data['_train']].assign(case='train').drop(columns=['predicted_proportion']),
    data[~data['_train']].assign(case='validation').drop(columns=['predicted_proportion']),
    data[~data['_train']].assign(case='predicted').drop(columns=['proportion']).rename(columns={'predicted_proportion': 'proportion'})
])

data["month"] = data["month"].apply(lambda m: MONTHS[m])

plot_df = data[data['_case'] == 'deep'].rename(columns={'radians': 'Radians', 'month': 'Month', 'proportion': 'Proportion', 'case': 'Case'})
plot_df['Case'] = plot_df['Case'].apply(lambda c: c.capitalize())
fig = px.scatter(
    plot_df, x='Radians', y='Proportion', color='Case',
    facet_col='Month', facet_col_wrap=4,
    category_orders={'Month': list(MONTHS.values())}, # title="Proportion Deeper than 25m by Time of Day",
    height=900, width=1000, color_discrete_map={
        'Train': 'blue', 'Validation': 'orange', 'Predicted': 'purple'
    }
)
fig.show()

In [20]:
fig.write_image("fig3_diel.png", format="png", scale=2)

In [21]:
sql = f'''
select
    cos_sun,
    sin_sun,
    tag_key,
    case 
        when depth_bin = 25 then 'shallow'
        else 'deep' 
    end as _case,
    sum(case when _selected then 1.0 else 0.0 end) as num_selected
from 
    chinook_depth_inference_{model_id}
where
    run_id = '{run_id}'
    and extract(month from time) = 8
group by 
    1, 2, 3, 4
'''
data = read_data_w_cache(sql)
data['radians'] = np.arctan2(data['sin_sun'], data['cos_sun'])
data['day'] = data['radians'] > 0
data = data.groupby(['tag_key', 'day', '_case'])[['num_selected']].sum().reset_index()
data['total_selected'] = data.groupby(['tag_key', 'day'])['num_selected'].transform('sum')
data['proportion'] = data['num_selected'] / data['total_selected']
print(data.shape)
data.head()

(112, 6)


tag_key    day    _case  num_selected  total_selected  proportion
0  133395  False     deep          23.0           810.0    0.028395
1  133395  False  shallow         787.0           810.0    0.971605
2  133395   True     deep         245.0          1318.0    0.185888
3  133395   True  shallow        1073.0          1318.0    0.814112
4  142189  False     deep          62.0           546.0    0.113553

In [22]:
px.histogram(data[data['_case'] == 'shallow'], x='proportion', color='day', barmode='group')

In [23]:
data['tag_key'].nunique()

28

In [24]:
data[data['day'] & (data['proportion'] > .70) & (data['_case'] == 'shallow')].reset_index(drop=True)

tag_key   day    _case  num_selected  total_selected  proportion
0  133395  True  shallow        1073.0          1318.0    0.814112
1  142189  True  shallow         858.0           984.0    0.871951
2  142191  True  shallow        1055.0          1167.0    0.904027
3  202586  True  shallow         109.0           145.0    0.751724

In [25]:
data[data['day'] & (data['proportion'] < .15) & (data['_case'] == 'shallow')].reset_index(drop=True)

tag_key   day    _case  num_selected  total_selected  proportion
0  202596  True  shallow         165.0          1130.0    0.146018
1  202601  True  shallow          65.0           849.0    0.076561
2  229227  True  shallow         228.0          1643.0    0.138771
3  229232  True  shallow         126.0          1502.0    0.083888
4  229234  True  shallow           0.0           839.0    0.000000
5  229240  True  shallow         246.0          1846.0    0.133261

In [26]:
data[data['day'] & (data['proportion'] < .3) & (data['_case'] == 'shallow')].reset_index(drop=True)

tag_key   day    _case  num_selected  total_selected  proportion
0  202588  True  shallow         306.0          1316.0    0.232523
1  202596  True  shallow         165.0          1130.0    0.146018
2  202601  True  shallow          65.0           849.0    0.076561
3  202602  True  shallow         458.0          1610.0    0.284472
4  229227  True  shallow         228.0          1643.0    0.138771
5  229231  True  shallow         103.0           593.0    0.173693
6  229232  True  shallow         126.0          1502.0    0.083888
7  229234  True  shallow           0.0           839.0    0.000000
8  229240  True  shallow         246.0          1846.0    0.133261

In [27]:
data[~data['day'] & (data['proportion'] < .50) & (data['_case'] == 'shallow')].reset_index(drop=True)

tag_key    day    _case  num_selected  total_selected  proportion
0  202592  False  shallow         497.0           999.0    0.497497
1  202600  False  shallow         441.0           948.0    0.465190
2  229231  False  shallow         129.0           417.0    0.309353
3  229234  False  shallow         137.0           392.0    0.349490

In [28]:
data[~data['day'] & (data['proportion'] > .85) & (data['_case'] == 'shallow')].reset_index(drop=True)

tag_key    day    _case  num_selected  total_selected  proportion
0  133395  False  shallow         787.0           810.0    0.971605
1  142189  False  shallow         484.0           546.0    0.886447
2  142191  False  shallow         624.0           727.0    0.858322
3  202585  False  shallow         903.0          1017.0    0.887906
4  202591  False  shallow         785.0           857.0    0.915986
5  202597  False  shallow         740.0           860.0    0.860465
6  202601  False  shallow         531.0           620.0    0.856452

## Salinity

In [29]:
sql = '''
select
    salinity
from 
    chinook_depth_inference_3_7_2
where 
    run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
    and depth_bin = 25
'''
boundary = read_data_w_cache(sql)['salinity'].quantile(0.25)
print(boundary)

31.33286156143288


In [44]:
sql = f'''
with surface_salinity as (
    select
        _individual,
        _decision,
        _train,
        salinity as surface_salinity
    from 
        chinook_depth_inference_3_7_2
    where 
        run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
        and depth_bin = 25
), max_depth_bins as (
    select
        _individual,
        _decision,
        _train,
        max(depth_bin) as max_depth_bin
    from 
        chinook_depth_inference_3_7_2
    where 
        run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
    group by 
        1, 2, 3
)
select
    extract(month from time) as month,
    max_depth_bin,
    case 
        when surface_salinity < {boundary} then 'low'
        else 'high'
    end as surface_salinity,
    sum(case when _selected then 1.0 else 0.0 end) as num_selected,
    sum(probability) as expected_num_selected,
    count(*) as samples
from 
    chinook_depth_inference_3_7_2
    inner join surface_salinity
        using (_individual, _decision, _train)
    inner join max_depth_bins
        using (_individual, _decision, _train)
where 
    run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
    and depth_bin = 25
group by 
    1, 2, 3      

'''
data = read_data_w_cache(sql)
# only get the months and depth bins in common
data = data.merge(
    data[data['surface_salinity'] == 'high'][['month', 'max_depth_bin']].merge(
        data[data['surface_salinity'] == 'low'][['month', 'max_depth_bin']]
    )
)
data['proportion'] = data['num_selected'] / data['samples']
data['predicted_proportion'] = data['expected_num_selected'] / data['samples']
data = data.groupby(['month', 'surface_salinity'])['predicted_proportion'].mean().reset_index()
print(data.shape)
data.head()

(24, 3)


month surface_salinity  predicted_proportion
0      1             high              0.505049
1      1              low              0.563849
2      2             high               0.57565
3      2              low               0.61402
4      3             high              0.578626

In [45]:
data["month"] = data["month"].apply(lambda m: MONTHS[m])
plot_df = data.rename(columns={'month': 'Month', 'predicted_proportion': 'Proportion', 'surface_salinity': 'Surface Salinity'})
plot_df.loc[plot_df['Surface Salinity'] == 'high', 'Surface Salinity'] = 'High (>=31.3ppt)'
plot_df.loc[plot_df['Surface Salinity'] == 'low', 'Surface Salinity'] = 'Low (<31.3ppt)'
fig = px.bar(
    plot_df, x='Month', y='Proportion', barmode='group', 
    color='Surface Salinity', category_orders={"Month": list(MONTHS.values())},
    #title="Predicted Proportion Near Surface by Surface Salinity",
    height=400, width=800
)
fig.show()

In [46]:
fig.write_image("fig4_salinity1.png", format="png", scale=2)

In [62]:
sql = '''
select 
    _train,
    extract(month from time) as month,
    avg(ln(probability)) as loss
from
    chinook_depth_inference_3_7_2
where 
    run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
    and _selected
group by 1, 2
order by 1
'''
salinity = read_data_w_cache(sql)
print(salinity.shape)
salinity.head()

(24, 3)


_train  month      loss
0   False      7 -1.419682
1   False     10 -1.565768
2   False      4 -1.228531
3   False      8 -1.254802
4   False      1 -1.729909

In [66]:
sql = '''
select 
    _train,
    extract(month from time) as month,
    avg(ln(probability)) as loss
from
    chinook_depth_inference_3_1_4
where 
    run_id = '00cf23b296999368ea18b82e33b8687c51e8c35e876afd325e26317cb69ea45b'
    and _selected
group by 1, 2
order by 1
'''
base = read_data_w_cache(sql)
base.head()

_train  month      loss
0   False      4 -1.262583
1   False      9 -1.240058
2   False     10 -1.569875
3   False     12 -1.628132
4   False      1 -1.677520

In [67]:
df = base.merge(salinity, on=['month', '_train'], suffixes=('', '_w_salinity'))
df['difference'] = -(df['loss_w_salinity'] - df['loss'])
df.sort_values(['month', '_train']).reset_index(drop=True)

_train  month      loss  loss_w_salinity  difference
0    False      1 -1.677520        -1.729909    0.052389
1     True      1 -1.465065        -1.414039   -0.051025
2    False      2 -1.786670        -1.649368   -0.137303
3     True      2 -1.508156        -1.508834    0.000678
4    False      3 -1.690566        -1.670576   -0.019990
5     True      3 -1.488626        -1.483531   -0.005096
6    False      4 -1.262583        -1.228531   -0.034052
7     True      4 -1.373454        -1.367545   -0.005909
8    False      5 -0.893778        -0.892486   -0.001292
9     True      5 -1.309779        -1.305329   -0.004450
10   False      6 -1.007523        -1.012155    0.004633
11    True      6 -1.005183        -1.008196    0.003013
12   False      7 -1.408486        -1.419682    0.011195
13    True      7 -1.376349        -1.374870   -0.001479
14   False      8 -1.267870        -1.254802   -0.013068
15    True      8 -1.213493        -1.183112   -0.030382
16   False      9 -1.240058        -1.223076   -0.016983
17    True      9 -1.284128        -1.273463   -0.010665
18   False     10 -1.569875        -1.565768   -0.004108
19    True     10 -1.488120        -1.433007   -0.055112
20   False     11 -1.635788        -1.546006   -0.089782
21    True     11 -1.607459        -1.508851   -0.098608
22   False     12 -1.628132        -1.652585    0.024453
23    True     12 -1.582960        -1.552323   -0.030637

In [68]:
df['month'] = df['month'].apply(lambda m: MONTHS[m])
plot_df = df.rename(columns={'difference': 'Change in Loss', 'month': 'Month'})
plot_df.loc[plot_df['_train'], 'Case'] = 'Train'
plot_df.loc[~plot_df['_train'], 'Case'] = 'Validation'
fig = px.bar(
    plot_df, x='Month', y='Change in Loss', color='Case', barmode='group',
    category_orders={'Month': list(MONTHS.values())},
    #title='Variation in Change in Loss with Salinity as a Feature',
    height=400, width=800
)
fig.show()

In [69]:
fig.write_image("fig5_salinity2.png", format="png", scale=2)

# Assessing Likelihood of Occupancy Near the Seafloor

## Spatial Distribution of Minimum Likelihood

In [70]:
sql = '''
with risk as (
    select 
        time, 
        epoch,
        h3_index,
        depth_bin,
        max(elevation) as elevation,
        sum(probability) as risk
    from 
        chinook_depth_full_inference_3_7_2
    where 
        run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
    group by 
        1, 2, 3, 4
), max_depth_bin as (
    select 
        time, 
        epoch,
        h3_index,
        max(depth_bin) as depth_bin
    from 
        chinook_depth_full_inference_3_7_2
    where 
        run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
    group by 
        1, 2, 3
)
select 
    month(time) as month,
    h3_index,
    depth_bin,
    elevation,
    approx_percentile(risk, 0.05) as min_risk_month,
    approx_percentile(risk, 0.95) as max_risk_month
from 
    risk inner join max_depth_bin using (time, epoch, h3_index, depth_bin)
group by 
    1, 2, 3, 4
'''
data = read_data_w_cache(sql)
data['lat'] = data['h3_index'].apply(lambda x: h3.h3_to_geo(x)[0])
data['lon'] = data['h3_index'].apply(lambda x: h3.h3_to_geo(x)[1])
print(data.shape)
data.head()

(18036, 8)


month         h3_index  depth_bin    elevation  min_risk_month  \
0      5  840cccdffffffff      100.0    13.271235        0.046133   
1      7  840cd09ffffffff       75.0   -68.996347        0.082439   
2      4  840cf13ffffffff       25.0   -10.645551        1.000000   
3      1  841da31ffffffff      500.0 -4203.381633        0.000178   
4      1  840c8ddffffffff       50.0   -36.545407        0.238170   

   max_risk_month        lat         lon  
0        0.104005  56.614374 -157.604818  
1        0.191915  57.034745 -165.000218  
2        1.000000  58.482995 -161.298967  
3        0.003582  54.990389 -148.591927  
4        0.390282  59.326105 -167.624415

In [71]:
data = data[data['depth_bin'] + 100 > -data['elevation']]
print(data.shape)

(7656, 8)


In [72]:
from shapely.geometry import Polygon, Point

poly = Polygon(
    [
        (-166, 54.4),
        (-160, 56),
        (-158, 57.2),
        (-153, 62),
        (-149, 62),
        (-146, 62),
        (-140, 60),
        (-136, 58.4),
        (-133, 57.5),
        (-132, 56.0),
        (-131, 55),
        (-125, 50.3),
        (-170, 52.5),
        (-166, 54.4),
    ]
)
data['inside_polygon'] = data.apply(lambda row: poly.contains(Point(row['lon'], row['lat'])), axis=1)
fig = px.scatter_mapbox(
    data[(data['month'] == 2)  & (data['depth_bin'] != 25.0)],
    lat='lat',
    lon='lon',
    color='inside_polygon',  # Color points by probability
    size_max=10,  # Adjust as needed
    zoom=3,  # Adjust zoom level
    mapbox_style="carto-positron",  # Choose a map style,
    range_color=[0.0, 0.3]
)
fig.show()

In [73]:
data = data[data['inside_polygon']]
data = data[data['lon'] < -145]
data['size'] = 0.01

In [74]:
fig = px.scatter_mapbox(
    data[(data['month'] == 2)  & (data['depth_bin'] != 25.0)],
    lat='lat',
    lon='lon',
    color='min_risk_month',  # Color points by probability
    size='size',  # Adjust as needed
    size_max=11,  # Adjust as needed
    zoom=4,  # Adjust zoom level
    mapbox_style="carto-positron",  # Choose a map style,
    title='Spatial Pattern of Minimal Probability in Bottom Depth Bin in February',
    #range_color=[0.0, 0.3],
    height=600,
    width=1000
)
fig.show()

In [75]:
fig = px.scatter_mapbox(
    data[(data['month'] == 8) & (data['depth_bin'] != 25.0)],
    lat='lat',
    lon='lon',
    color='min_risk_month',  # Color points by probability
    size='size',  # Adjust as needed
    size_max=11,  # Adjust as needed
    zoom=4,  # Adjust zoom level
    mapbox_style="carto-positron",  # Choose a map style,
    title='Spatial Pattern of Minimal Probability in Bottom Depth Bin in August',
    #range_color=[0.0, 0.3],
    height=600,
    width=1000
)
fig.show()

In [77]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Create subplot figure with 1 row and 2 columns
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('February', 'August'),
    specs=[[{'type': 'mapbox'}, {'type': 'mapbox'}]],
    horizontal_spacing=0.01
)

# Prepare February data
feb_data = data[(data['month'] == 2) & (data['depth_bin'] != 25.0)]

# Prepare August data
aug_data = data[(data['month'] == 8) & (data['depth_bin'] != 25.0)]

color_min = min(feb_data['min_risk_month'].min(), aug_data['min_risk_month'].min())
color_max = max(feb_data['min_risk_month'].max(), aug_data['min_risk_month'].max())


# Add February trace
fig.add_trace(
    go.Scattermapbox(
        lat=feb_data['lat'],
        lon=feb_data['lon'],
        mode='markers',
        marker=dict(
            size=feb_data['size'],
            sizemode='diameter',
            sizeref=2.*max(feb_data['size'])/30,
            color=feb_data['min_risk_month'],
            colorscale='plasma',  # Adjust colorscale as needed
            showscale=False,
            cmin=color_min,
            cmax=color_max,
        ),
        text=feb_data['min_risk_month'],
        hovertemplate='<b>Lat:</b> %{lat}<br><b>Lon:</b> %{lon}<br><b>Value:</b> %{text}<extra></extra>'
    ),
    row=1, col=1
)

# Add August trace
fig.add_trace(
    go.Scattermapbox(
        lat=aug_data['lat'],
        lon=aug_data['lon'],
        mode='markers',
        marker=dict(
            size=aug_data['size'],
            sizemode='diameter',
            sizeref=2.*max(aug_data['size'])/30,
            color=aug_data['min_risk_month'],
            colorscale='plasma',
            showscale=True,
            cmin=color_min,
            cmax=color_max,
            colorbar=dict(x=1.02, len=0.5)
        ),
        text=aug_data['min_risk_month'],
        hovertemplate='<b>Lat:</b> %{lat}<br><b>Lon:</b> %{lon}<br><b>Value:</b> %{text}<extra></extra>'
    ),
    row=1, col=2
)

# Update mapbox layouts
fig.update_mapboxes(
    style="carto-positron",
    zoom=4,
    center=dict(lat=feb_data['lat'].mean(), lon=feb_data['lon'].mean())
)

# Update overall layout
fig.update_layout(
    #title_text='Spatial Distribution of Minimal Likelihood in Bottom Depth Bin',
    title_x=0.5,
    height=600,
    width=1600,
    showlegend=False
)

fig.show()

In [78]:
fig.write_image("fig6_spatial_risk.png", format="png", scale=2)

## Full Year of Likelihoods

In [79]:
h3_indices = {
    'Chignik': {
        'Coastal': '840ccebffffffff',
    }
}

sql = '''
select 
    epoch, h3_index, depth_bin, probability
from 
    chinook_depth_full_inference_3_7_2
where 
    run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
    and h3_index = '{h3_index}'
'''
dfs = []
for place, cases in h3_indices.items():
    for case, h3_index in cases.items():
        data = read_data_w_cache(sql.format(h3_index=h3_index))
        data['time'] = pd.to_datetime(data['epoch'], unit='s', utc=False)
        # convert to alaska time
        data['time'] = data['time'].dt.tz_localize('UTC').dt.tz_convert('America/Anchorage')
        data['place'] = place
        data['case'] = case
        print(data.shape)
        dfs.append(data)
data = pd.concat(dfs).reset_index(drop=True)
print(data.shape)
data.head()

(35040, 7)
(35040, 7)


epoch         h3_index  depth_bin  probability  \
0  1670662800  840ccebffffffff      100.0     0.099453   
1  1643504400  840ccebffffffff      100.0     0.141165   
2  1641978000  840ccebffffffff       50.0     0.180613   
3  1643504400  840ccebffffffff       25.0     0.494927   
4  1651885200  840ccebffffffff       75.0     0.073720   

                       time    place     case  
0 2022-12-10 00:00:00-09:00  Chignik  Coastal  
1 2022-01-29 16:00:00-09:00  Chignik  Coastal  
2 2022-01-12 00:00:00-09:00  Chignik  Coastal  
3 2022-01-29 16:00:00-09:00  Chignik  Coastal  
4 2022-05-06 17:00:00-08:00  Chignik  Coastal

In [83]:
color_discrete_map = {
    25.0: "#c7e9c0",  # Light Green
    50.0: "#a1d99b",  
    75.0: "#74c476",  
    100.0: "#41ab5d",  
    150.0: "#238b45",  
    200.0: "#1b7837",  
    250.0: "#0868ac",  
    300.0: "#08519c",  
    400.0: "#08306b",  # Deep Blue
    500.0: "#041c40",  # Darkest Blue (Deepest)
}

depth_order = sorted(color_discrete_map.keys())
data['depth_bin'] = pd.Categorical(data['depth_bin'], categories=depth_order, ordered=True)
data['likelihood'] = data['probability']

plot_df = data.rename(columns={'likelihood': 'Likelihood', 'depth_bin': 'Depth Bin (m)', 'time': 'Time'})

# Now plot with the correct legend order
fig = px.line(
    plot_df.sort_values('Time'), x='Time', y='Likelihood', color='Depth Bin (m)',
    color_discrete_map=color_discrete_map,
    category_orders={"Depth Bin (m)": sorted(color_discrete_map.keys())},
    #title='Likelihood per Depth Bin near Chignik',
    height=400, width=1000
)

fig.show()


In [84]:
fig.write_image("fig8_full_year.png", format="png", scale=2)

## Time of Day Minimization

In [85]:
sql = '''
with risk as (
    select 
        month(time) as month, 
        epoch,
        h3_index,
        depth_bin,
        sin_sun,
        cos_sun,
        max(elevation) as elevation,
        sum(probability) as risk
    from 
        chinook_depth_full_inference_3_7_2
    where 
        run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
        and day(time) = 15
    group by 
        1, 2, 3, 4, 5, 6
), max_depth_bin as (
    select 
        month(time) as month, 
        epoch,
        h3_index,
        max(depth_bin) as depth_bin
    from 
        chinook_depth_full_inference_3_7_2
    where 
        run_id = 'fb3f06dc5fd0971a4e7cfdd2e5da5cca391a633f92528e79aa526df347ca0920'
    group by 
        1, 2, 3
), boundaries as (
    select 
        month,
        h3_index,
        depth_bin,
        elevation,
        approx_percentile(risk, 0.05) as min_risk_month,
        approx_percentile(risk, 0.95) as max_risk_month
    from 
        risk inner join max_depth_bin using (month, epoch, h3_index, depth_bin)
    group by 
        1, 2, 3, 4
), joined as (
    select 
        r.month,
        r.h3_index,
        r.sin_sun, 
        r.cos_sun,
        r.risk,
        b.depth_bin,
        b.elevation,
        b.min_risk_month,
        b.max_risk_month
    from 
        risk r
        inner join boundaries b 
            on r.month = b.month
            and r.h3_index = b.h3_index
)
select 
    month,
    h3_index,
    depth_bin,
    elevation,
    avg(sin_sun) as avg_sin_sun,
    avg(cos_sun) as avg_cos_sun
from 
    joined 
where 
    risk <= min_risk_month
group by 
    1, 2, 3, 4
'''
data = read_data_w_cache(sql)
data['lat'] = data['h3_index'].apply(lambda x: h3.h3_to_geo(x)[0])
data['lon'] = data['h3_index'].apply(lambda x: h3.h3_to_geo(x)[1])
print(data.shape)
data.head()

(18036, 8)


month         h3_index  depth_bin    elevation  avg_sin_sun  avg_cos_sun  \
0     11  840ca91ffffffff       25.0    21.704028    -0.244073    -0.000036   
1     10  841d209ffffffff      200.0   -47.937292    -0.853136    -0.508769   
2     12  841da2bffffffff      500.0 -4316.299883    -0.805162    -0.585747   
3     12  841d0bdffffffff      500.0 -3666.231098    -0.862007    -0.497680   
4      5  841da43ffffffff      500.0 -3981.155422    -0.972012    -0.114366   

         lat         lon  
0  60.686211 -165.328277  
1  56.904717 -135.606640  
2  55.562718 -149.140745  
3  52.390967 -139.160837  
4  56.472439 -147.310216

In [86]:
data = data[data['depth_bin'] + 100 > -data['elevation']]
data['inside_polygon'] = data.apply(lambda row: poly.contains(Point(row['lon'], row['lat'])), axis=1)
data = data[data['inside_polygon']]
data = data[data['lon'] < -145]
data['size'] = 0.01

In [87]:
data['sun_is_up'] = np.sign(data['avg_sin_sun'])
fig = px.scatter_mapbox(
    data[(data['month'] == 2) & (data['depth_bin'] != 25.0)],
    lat='lat',
    lon='lon',
    color='avg_sin_sun',  # Color points by probability
    size='size',  # Adjust as needed
    size_max=11,  # Adjust as needed
    zoom=4,  # Adjust zoom level
    mapbox_style="carto-positron",  # Choose a map style,
    title='Spatial Pattern of Time of Minimal Risk in February',
    range_color=[-1, 1],
    height=600,
    width=1000,
    color_continuous_scale='RdBu_r',  # Red to Blue color scale
)
fig.show()

In [88]:
data['sun_is_up'] = np.sign(data['avg_sin_sun'])
fig = px.scatter_mapbox(
    data[(data['month'] == 8) & (data['depth_bin'] != 25.0)],
    lat='lat',
    lon='lon',
    color='avg_sin_sun',  # Color points by probability
    size='size',  # Adjust as needed
    size_max=11,  # Adjust as needed
    zoom=4,  # Adjust zoom level
    mapbox_style="carto-positron",  # Choose a map style,
    title='Spatial Pattern of Time of Minimal Risk in August',
    range_color=[-1, 1],
    height=600,
    width=1000,
    color_continuous_scale='RdBu_r',  # Red to Blue col.3or scale
)
fig.show()

In [90]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Create subplot figure with 1 row and 2 columns
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('February', 'August'),
    specs=[[{'type': 'mapbox'}, {'type': 'mapbox'}]],
    horizontal_spacing=0.01
)

# Prepare February data
feb_data = data[(data['month'] == 2) & (data['depth_bin'] != 25.0)]

# Prepare August data
aug_data = data[(data['month'] == 8) & (data['depth_bin'] != 25.0)]

# Use fixed color range
color_min = -1
color_max = 1

# Add February trace
fig.add_trace(
    go.Scattermapbox(
        lat=feb_data['lat'],
        lon=feb_data['lon'],
        mode='markers',
        marker=dict(
            size=feb_data['size'],
            sizemode='diameter',
            sizeref=2.*max(feb_data['size'])/30,
            color=feb_data['avg_sin_sun'],
            colorscale='RdBu_r',
            showscale=False,
            cmin=color_min,
            cmax=color_max,
        ),
        text=feb_data['avg_sin_sun'],
        hovertemplate='<b>Lat:</b> %{lat}<br><b>Lon:</b> %{lon}<br><b>Value:</b> %{text}<extra></extra>'
    ),
    row=1, col=1
)

# Add August trace
fig.add_trace(
    go.Scattermapbox(
        lat=aug_data['lat'],
        lon=aug_data['lon'],
        mode='markers',
        marker=dict(
            size=aug_data['size'],
            sizemode='diameter',
            sizeref=2.*max(aug_data['size'])/30,
            color=aug_data['avg_sin_sun'],
            colorscale='RdBu_r',
            showscale=True,
            cmin=color_min,
            cmax=color_max,
            colorbar=dict(x=1.02, len=0.5)
        ),
        text=aug_data['avg_sin_sun'],
        hovertemplate='<b>Lat:</b> %{lat}<br><b>Lon:</b> %{lon}<br><b>Value:</b> %{text}<extra></extra>'
    ),
    row=1, col=2
)

# Update mapbox layouts
fig.update_mapboxes(
    style="carto-positron",
    zoom=4,
    center=dict(lat=feb_data['lat'].mean(), lon=feb_data['lon'].mean())
)

# Update overall layout
fig.update_layout(
    #title_text='Spatial Pattern of Time of Minimal Likelihood',
    title_x=0.5,
    height=600,
    width=1600,
    showlegend=False
)

fig.show()

In [91]:
fig.write_image("fig7_time_risk.png", format="png", scale=2)

## Paths

In [98]:
sql = '''
select
    tag_key, epoch, longitude, latitude
from 
    mgietzmann_tag_tracks
where
    upload_key = 'mgietzmann'
'''
data = read_data_w_cache(sql)
data["month"] = pd.to_datetime(data["epoch"], unit="s").dt.month
print(data.shape)
data.head()

(7532, 5)


tag_key       epoch   longitude   latitude  month
0  129843  1387411200 -166.922615  54.131760     12
1  129843  1387497600 -166.884086  54.258072     12
2  129843  1387584000 -166.910525  54.312433     12
3  129843  1387670400 -166.817057  54.358280     12
4  129843  1387756800 -166.676901  54.389694     12

In [103]:
import plotly.graph_objects as go

plot_df = data.rename(columns={'month': 'Month'})
fig = px.scatter_map(
    plot_df, lat='latitude', lon='longitude',
    zoom=3, center=dict(lat=data['latitude'].mean(), lon=data['longitude'].mean()),
    height=700, width=1000, color="Month"
)

starts = data.sort_values('epoch').groupby('tag_key').first().reset_index()

fig.add_trace(
    go.Scattermap(
        lat=starts['latitude'],
        lon=starts['longitude'],
        mode='markers',
        marker=dict(size=12, color='black'),
        name='Start',
        showlegend=False
    )
)

fig.show()

In [104]:
fig.write_image("fig1_tracks.png", format="png", scale=2)